In [ ]:
!pip install flair

In [ ]:
from flair.datasets import CONLL_03
from flair.data import Corpus, Sentence
from flair.datasets import ColumnCorpus
from flair.embeddings import TransformerWordEmbeddings
from flair.models import SequenceTagger
from flair.trainers import ModelTrainer

import pandas as pd

from sklearn.model_selection import train_test_split

In [ ]:
in_path = '/content/drive/MyDrive/Proyecto_ConflictoArmado/NER/output.txt'

# Abre el archivo de texto en modo lectura
with open(in_path, 'r', encoding='utf-8') as file:
    # Lee las líneas del archivo
    lines = file.readlines()

# Inicializa el DataFrame
data = {'sentence_id': [], 'text': [], 'tag': []}

# Inicializa el identificador de oración
sentence_id = 1

# Procesa cada línea del archivo
for line in lines:
    line = line.strip()  # Elimina espacios en blanco al principio y al final de la línea
    if line:  # Si la línea no está en blanco
        parts = line.split()  # Divide la línea en palabras y etiquetas
        if len(parts) == 2:
            word, tag = parts
            data['sentence_id'].append(sentence_id)
            data['text'].append(word)
            data['tag'].append(tag)
        else:
            # Handle empty lines
            data['sentence_id'].append(None)
            data['text'].append(None)
            data['tag'].append(None)
    else:
        # Incrementa el identificador de oración al encontrar una línea en blanco
        sentence_id += 1

# Crea el DataFrame
df = pd.DataFrame(data)

umbral_longitud = 50

# Filtrar las oraciones por longitud dentro de cada grupo de sentence_id
df_filtrado = df.groupby('sentence_id').filter(lambda group: len(group) < umbral_longitud)

# Imprimir el DataFrame resultante
df_filtrado

sentence_id          text     tag
0              1.0      Naciones   B-ORG
1              1.0        Unidas   I-ORG
2              1.0      Asamblea       O
3              1.0       General       O
4              1.0            23  B-DATE
...            ...           ...     ...
88927        658.0           los       O
88928        658.0         niños   B-PER
88929        658.0         niñas   B-PER
88930        658.0             y       O
88931        658.0  adolescentes   B-PER

[14485 rows x 3 columns]

In [ ]:
to_replace = ['B-'+tag for tag in ['CON', 'ATE', 'MEM', 'LUC', 'EVE', 'DER', 'LEY']]
to_replace.extend(['I-'+tag for tag in ['CON', 'ATE', 'MEM', 'LUC', 'EVE', 'DER', 'LEY']])
df_filtrado['new_tag'] = df_filtrado['tag'].replace(to_replace, 'O')

In [ ]:
# Split the DataFrame into train, test, and dev sets based on sentence_ids
train_ids, test_ids = train_test_split(df_filtrado['sentence_id'].unique(), test_size=0.2, random_state=42)
train_ids, dev_ids = train_test_split(train_ids, test_size=0.1, random_state=42)

# Define a function to format rows as "word label"
def format_row(word, label):
    return f"{word} {label}"

# Save data into separate files based on sentence_ids
for split_name, split_ids in [('train', train_ids), ('test', test_ids), ('dev', dev_ids)]:
    split_data = df_filtrado[df_filtrado['sentence_id'].isin(split_ids)]

    formatted_rows = []
    for _, row in split_data.groupby('sentence_id'):
        formatted_rows.extend([format_row(word, label) for word, label in zip(row['text'], row['new_tag'])])
        formatted_rows.append("")  # Append a blank line after each sentence

    with open(f'{split_name}.txt', 'w') as file:
        file.write('\n'.join(formatted_rows))

In [ ]:
# 1. get the corpus
# define columns
columns = {0 : 'text', 1 : 'ner'}

# directory where the data resides
data_folder = '/content/'

# initializing the corpus
corpus: Corpus = ColumnCorpus(data_folder, columns,
                              train_file = 'train.txt',
                              test_file = 'test.txt',
                              dev_file = 'dev.txt')

2023-09-20 16:39:04,538 Reading data from /content
2023-09-20 16:39:04,541 Train: /content/train.txt
2023-09-20 16:39:04,542 Dev: /content/dev.txt
2023-09-20 16:39:04,544 Test: /content/test.txt


In [ ]:
# 2. what label do we want to predict?
label_type = 'ner'

In [ ]:
# 3. make the label dictionary from the corpus
label_dict = corpus.make_label_dictionary(label_type=label_type, add_unk=False)
print(label_dict)

2023-09-20 16:39:05,130 Computing label dictionary. Progress:


378it [00:00, 12320.75it/s]

2023-09-20 16:39:05,181 Dictionary created for label 'ner' with 8 values: PER (seen 164 times), GEO (seen 116 times), VIO (seen 113 times), ORG (seen 102 times), ARM (seen 65 times), PAZ (seen 42 times), DATE (seen 40 times), AFE (seen 33 times)
Dictionary with 8 tags: PER, GEO, VIO, ORG, ARM, PAZ, DATE, AFE


In [ ]:
# 4. initialize fine-tuneable transformer embeddings WITH document context
embeddings = TransformerWordEmbeddings(model='xlm-roberta-large',
                                       layers="-1",
                                       subtoken_pooling="first",
                                       fine_tune=True,
                                       use_context=True,
                                       )

In [ ]:
# 5. initialize bare-bones sequence tagger (no CRF, no RNN, no reprojection)
tagger = SequenceTagger(hidden_size=256,
                        embeddings=embeddings,
                        tag_dictionary=label_dict,
                        tag_type='ner',
                        use_crf=False,
                        use_rnn=False,
                        reproject_embeddings=False,
                        tag_format='BIO')

2023-09-20 16:39:27,403 SequenceTagger predicts: Dictionary with 17 tags: O, B-PER, I-PER, B-GEO, I-GEO, B-VIO, I-VIO, B-ORG, I-ORG, B-ARM, I-ARM, B-PAZ, I-PAZ, B-DATE, I-DATE, B-AFE, I-AFE


In [ ]:
# 6. initialize trainer
trainer = ModelTrainer(tagger, corpus)

In [ ]:
# 7. run fine-tuning
trainer.fine_tune('ner-bertSpanish-fineTuning2',
                  learning_rate=5.0e-6,
                  mini_batch_size=4,
                  mini_batch_chunk_size=1,  # remove this parameter to speed up computation if you have a big GPU
                  )

2023-09-20 16:39:27,431 ----------------------------------------------------------------------------------------------------
2023-09-20 16:39:27,447 Model: "SequenceTagger(
  (embeddings): TransformerWordEmbeddings(
    (model): XLMRobertaModel(
      (embeddings): XLMRobertaEmbeddings(
        (word_embeddings): Embedding(250003, 1024)
        (position_embeddings): Embedding(514, 1024, padding_idx=1)
        (token_type_embeddings): Embedding(1, 1024)
        (LayerNorm): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
        (dropout): Dropout(p=0.1, inplace=False)
      )
      (encoder): XLMRobertaEncoder(
        (layer): ModuleList(
          (0-23): 24 x XLMRobertaLayer(
            (attention): XLMRobertaAttention(
              (self): XLMRobertaSelfAttention(
                (query): Linear(in_features=1024, out_features=1024, bias=True)
                (key): Linear(in_features=1024, out_features=1024, bias=True)
                (value): Linear(in_features=1024, out

100%|██████████| 11/11 [00:02<00:00,  4.94it/s]

2023-09-20 16:40:46,340 Evaluating as a multi-label problem: False
2023-09-20 16:40:46,359 DEV : loss 0.6564602851867676 - f1-score (micro avg)  0.0
2023-09-20 16:40:46,363 ----------------------------------------------------------------------------------------------------


2023-09-20 16:40:52,692 epoch 2 - iter 9/95 - loss 0.68008748 - time (sec): 6.33 - samples/sec: 164.03 - lr: 0.000005
2023-09-20 16:40:59,736 epoch 2 - iter 18/95 - loss 0.82214551 - time (sec): 13.37 - samples/sec: 150.47 - lr: 0.000005
2023-09-20 16:41:06,257 epoch 2 - iter 27/95 - loss 0.84081419 - time (sec): 19.89 - samples/sec: 151.82 - lr: 0.000005
2023-09-20 16:41:13,054 epoch 2 - iter 36/95 - loss 0.82311766 - time (sec): 26.69 - samples/sec: 149.50 - lr: 0.000005
2023-09-20 16:41:21,216 epoch 2 - iter 45/95 - loss 0.85481312 - time (sec): 34.85 - samples/sec: 144.73 - lr: 0.000005
2023-09-20 16:41:27,552 epoch 2 - iter 54/95 - loss 0.83370049 - time (sec): 41.19 - samples/sec: 143.63 - lr: 0.000005
2023-09-20 16:41:34,547 epoch 2 - iter 63/95 - loss 0.81702753 - time (sec): 48.18 - samples/sec: 141.57 - lr: 0.000005
2023-09-20 16:41:40,865 epoch 2 - iter 72/95 - loss 0.83400647 - time (sec): 54.50 - samples/sec: 142.35 - lr: 0.000005
2023-09-20 16:41:47,553 epoch 2 - iter 81/

100%|██████████| 11/11 [00:02<00:00,  4.83it/s]

...

2023-09-20 16:51:48,360 Evaluating as a multi-label problem: False
2023-09-20 16:51:48,376 DEV : loss 0.35039085149765015 - f1-score (micro avg)  0.2313


2023-09-20 16:51:58,375 ----------------------------------------------------------------------------------------------------
2023-09-20 16:51:58,380 Testing using last state of model ...


100%|██████████| 27/27 [00:05<00:00,  5.28it/s]

2023-09-20 16:52:03,500 Evaluating as a multi-label problem: False
2023-09-20 16:52:03,518 0.367	0.3941	0.38	0.2424
2023-09-20 16:52:03,519 
Results:
- F-score (micro) 0.38
- F-score (macro) 0.271
- Accuracy 0.2424

By class:
              precision    recall  f1-score   support

         PER     0.2029    0.3256    0.2500        43
         VIO     0.4894    0.6216    0.5476        37
         ORG     0.4524    0.5429    0.4935        35
         GEO     0.4222    0.6333    0.5067        30
         ARM     0.5556    0.2778    0.3704        18
         PAZ     0.0000    0.0000    0.0000        19
         AFE     0.0000    0.0000    0.0000        11
        DATE     0.0000    0.0000    0.0000        10

   micro avg     0.3670    0.3941    0.3800       203
   macro avg     0.2653    0.3001    0.2710       203
weighted avg     0.3218    0.3941    0.3456       203

2023-09-20 16:52:03,521 ---------------------------------------------------------------------------------------------------

{'test_score': 0.3800475059382424,
 'dev_score_history': [0.0,
  0.0,
  0.0,
  0.0,
  0.02564102564102564,
  0.2285714285714286,
  0.22222222222222224,
  0.23129251700680276,
  0.2251655629139073,
  0.23129251700680276],
 'train_loss_history': [2.2083096445195376,
  0.7905150630989667,
  0.6759139882288138,
  0.6174707539115155,
  0.5402019214430303,
  0.49300472509990656,
  0.4592541911305255,
  0.4060959751833173,
  0.3825031868616195,
  0.3679287539225993],
 'dev_loss_history': [0.6564602851867676,
  0.5198074579238892,
  0.4649089276790619,
  0.4446188509464264,
  0.4345150291919708,
  0.38467857241630554,
  0.3640497028827667,
  0.3643392324447632,
  0.3552079200744629,
  0.35039085149765015]}

In [ ]:
# load the trained model
model = SequenceTagger.load('/content/resources/taggers/sota-ner-flert/final-model.pt')

# create example sentence
sentence = Sentence('Los principales perpetradores de esta violación fueron los paramilitares seguidos de guerrillas como las FARC y el ELN y fuerza pública y otros agentes del Estado como los organismos de inteligencia')# predict the tags
sentence2 = Sentence('Hola. Mi nombre es David Cortés, tengo 27 años de edad y soy de Tumaco, Nariño. Llegué a Bogotá cuando tenía 17 años por temas de seguridad. Mi mamá me envío a esta ciudad porque mi vida estaba en riesgo luego de que, por accidente, fuera testigo de la muerte de un narcotraficante. Todo el barrio estaba lleno de narcos')
sentence3 = Sentence('Mi mamá me envío a esta ciudad porque mi vida estaba en riesgo luego de que, por accidente, fuera testigo de la muerte de un narcotraficante. Todo el barrio estaba lleno de narcos')
model.predict(sentence)
model.predict(sentence2)
model.predict(sentence3)

print(sentence.to_tagged_string())
print(sentence2.to_tagged_string())
print(sentence3.to_tagged_string())